In [1]:
import pandas as pd
import numpy as np
import model_day
import model_30m
import model_1h
import model_90m

Found cached dataset text (C:/Users/WINSTON-ITX/.cache/huggingface/datasets/boomsss___text/boomsss--SPX_full_30min-37ae67efd8a1cc91/0.0.0/cb1e9bd71a82ad27976be3b12b407850fe2837d80c22c5e03a28949843a8ace2)


In [2]:
_, df_final_day, _ = model_day.get_data()
_, df_final_30m, _ = model_30m.get_data()
_, df_final_1h, _ = model_1h.get_data()
_, df_final_90m, _ = model_90m.get_data()

Making indicators: 100%|██████████| 8/8 [00:00<00:00, 7985.35it/s]
Found cached dataset text (C:/Users/WINSTON-ITX/.cache/huggingface/datasets/boomsss___text/boomsss--SPX_full_30min-37ae67efd8a1cc91/0.0.0/cb1e9bd71a82ad27976be3b12b407850fe2837d80c22c5e03a28949843a8ace2)
Making indicators: 100%|██████████| 8/8 [00:00<00:00, 3995.05it/s]
Found cached dataset text (C:/Users/WINSTON-ITX/.cache/huggingface/datasets/boomsss___text/boomsss--SPX_full_30min-37ae67efd8a1cc91/0.0.0/cb1e9bd71a82ad27976be3b12b407850fe2837d80c22c5e03a28949843a8ace2)
Making indicators: 100%|██████████| 8/8 [00:00<00:00, 3996.00it/s]
Found cached dataset text (C:/Users/WINSTON-ITX/.cache/huggingface/datasets/boomsss___text/boomsss--SPX_full_30min-37ae67efd8a1cc91/0.0.0/cb1e9bd71a82ad27976be3b12b407850fe2837d80c22c5e03a28949843a8ace2)
Merging econ data: 100%|██████████| 8/8 [00:00<00:00, 999.18it/s]


In [3]:
res_day, _, _ = model_day.walk_forward_validation_seq(df_final_day.dropna(axis=0), 'Target_clf', 'Target', 100, 1)
res_30m, _, _ = model_30m.walk_forward_validation_seq(df_final_30m.dropna(axis=0), 'Target_clf', 'Target', 100, 1)
res_1h, _, _ = model_1h.walk_forward_validation_seq(df_final_1h.dropna(axis=0), 'Target_clf', 'Target', 100, 1)
res_90m, _, _ = model_90m.walk_forward_validation_seq(df_final_90m.dropna(axis=0), 'Target_clf', 'Target', 100, 1)

LR Model: 100%|██████████| 1177/1177 [00:03<00:00, 391.99it/s]
d:\Projects\gamedayspx\model_day.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  for_merge['RegrModelOut'] = for_merge['RegrModelOut'] > 0
LR Model: 100%|██████████| 1177/1177 [00:03<00:00, 367.13it/s]
d:\Projects\gamedayspx\model_30m.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  for_merge['RegrModelOut'] = for_merge['RegrModelOut'] > 0
LR Model: 100%|██████████| 1177/1177 [00:03<00:00, 351.68it/s]
d:\Projects\gamedayspx\model_1h.py:

In [6]:
res_day

True  Predicted
index                       
2019-04-23  False   0.798423
2019-04-24  False   0.235411
2019-04-25   True   0.479671
2019-04-26   True   0.180924
2019-04-29   True   0.457531
...           ...        ...
2023-07-26  False   0.863622
2023-07-27   True   0.875761
2023-07-28   True   0.506219
2023-07-31  False   0.273154
2023-08-01  False   0.238163

[1077 rows x 2 columns]

In [18]:
for df in [res_day, res_30m, res_1h, res_90m]:
    df['HighConfidence'] = [True if x > 0.6 or x <= 0.4 else False for x in df['Predicted']]
    df['PredDirection'] = df['Predicted'] > 0.5
    df['Correct'] = df['PredDirection'] == df['True']
    df['RedDays'] = df['True'] == False
    df['GreenDays'] = df['True'] == True

In [20]:
res_day

True  Predicted  HighConfidence  PredDirection  RedDays  \
index                                                                  
2019-04-23  False   0.798423            True           True     True   
2019-04-24  False   0.235411            True          False     True   
2019-04-25   True   0.479671           False          False    False   
2019-04-26   True   0.180924            True          False    False   
2019-04-29   True   0.457531           False          False    False   
...           ...        ...             ...            ...      ...   
2023-07-26  False   0.863622            True           True     True   
2023-07-27   True   0.875761            True           True    False   
2023-07-28   True   0.506219           False           True    False   
2023-07-31  False   0.273154            True          False     True   
2023-08-01  False   0.238163            True          False     True   

            GreenDays  Correct  
index                           
2019-04-23      False    False  
2019-04-24      False     True  
2019-04-25       True    False  
2019-04-26       True    False  
2019-04-29       True    False  
...               ...      ...  
2023-07-26      False    False  
2023-07-27       True     True  
2023-07-28       True     True  
2023-07-31      False     True  
2023-08-01      False     True  

[1077 rows x 7 columns]

In [35]:
all_res = pd.concat([res_day.drop(columns=['GreenDays','RedDays']), res_30m.drop(columns=['GreenDays','RedDays']), res_90m.drop(columns=['GreenDays','RedDays']), res_1h.drop(columns=['GreenDays','RedDays']), res_day[['GreenDays','RedDays']]], axis=1)

In [36]:
all_res1 = all_res[['HighConfidence','PredDirection','Correct','GreenDays','RedDays']]

In [37]:
all_res1

HighConfidence  HighConfidence  HighConfidence  HighConfidence  \
2019-04-23            True            True            True            True   
2019-04-24            True            True            True            True   
2019-04-25           False            True            True           False   
2019-04-26            True            True            True            True   
2019-04-29           False            True            True            True   
...                    ...             ...             ...             ...   
2023-07-26            True            True            True            True   
2023-07-27            True            True            True            True   
2023-07-28           False           False            True            True   
2023-07-31            True            True            True            True   
2023-08-01            True            True            True            True   

            PredDirection  PredDirection  PredDirection  PredDirection  \
2019-04-23           True          False           True           True   
2019-04-24          False          False          False          False   
2019-04-25          False          False           True           True   
2019-04-26          False           True           True           True   
2019-04-29          False          False          False          False   
...                   ...            ...            ...            ...   
2023-07-26           True           True           True           True   
2023-07-27           True           True           True           True   
2023-07-28           True           True           True           True   
2023-07-31          False          False          False          False   
2023-08-01          False          False          False          False   

            Correct  Correct  Correct  Correct  GreenDays  RedDays  
2019-04-23    False     True    False    False      False     True  
2019-04-24     True     True     True     True      False     True  
2019-04-25    False    False     True     True       True    False  
2019-04-26    False     True     True     True       True    False  
2019-04-29    False    False    False    False       True    False  
...             ...      ...      ...      ...        ...      ...  
2023-07-26    False    False    False    False      False     True  
2023-07-27     True     True     True     True       True    False  
2023-07-28     True     True     True     True       True    False  
2023-07-31     True     True     True     True      False     True  
2023-08-01     True     True     True     True      False     True  

[1077 rows x 14 columns]

In [38]:
all_res1.columns = [
    'HighConfidence_day',
    'HighConfidence_30m',
    'HighConfidence_1h',
    'HighConfidence_90m',
    'PredDirection_day',
    'PredDirection_30m',
    'PredDirection_1h',
    'PredDirection_90m',
    'Correct_day',
    'Correct_30m',
    'Correct_1h',
    'Correct_90m',
    'GreenDays',
    'RedDays'
]

In [41]:
# When all models pred green, how often was it green?
all_res1.query('''
    PredDirection_day == True & PredDirection_30m == True & PredDirection_1h == True & PredDirection_90m == True
''')['GreenDays'].sum() / len(all_res1.query('''
    PredDirection_day == True & PredDirection_30m == True & PredDirection_1h == True & PredDirection_90m == True
'''))

0.8133333333333334

In [42]:
# When all models pred red, how often was it red?
all_res1.query('''
    PredDirection_day == False & PredDirection_30m == False & PredDirection_1h == False & PredDirection_90m == False
''')['RedDays'].sum() / len(all_res1.query('''
    PredDirection_day == False & PredDirection_30m == False & PredDirection_1h == False & PredDirection_90m == False
'''))

0.8638297872340426

In [57]:
# When all models are pred green with high confidendce, how often was it green?
print(all_res1.query('''
    HighConfidence_day == True & HighConfidence_30m == True & HighConfidence_1h == True & HighConfidence_90m == True & \
    PredDirection_day == True & PredDirection_30m == True & PredDirection_1h == True & PredDirection_90m == True
''')['GreenDays'].sum()  / len(all_res1.query('''
    HighConfidence_day == True & HighConfidence_30m == True & HighConfidence_1h == True & HighConfidence_90m == True & \
    PredDirection_day == True & PredDirection_30m == True & PredDirection_1h == True & PredDirection_90m == True
 ''')))

print(all_res1.query('''
    HighConfidence_day == True & HighConfidence_30m == True & HighConfidence_1h == True & HighConfidence_90m == True & \
    PredDirection_day == True & PredDirection_30m == True & PredDirection_1h == True & PredDirection_90m == True
''')['GreenDays'].sum())

print(len(all_res1.query('''
    HighConfidence_day == True & HighConfidence_30m == True & HighConfidence_1h == True & HighConfidence_90m == True & \
    PredDirection_day == True & PredDirection_30m == True & PredDirection_1h == True & PredDirection_90m == True
 ''')))


0.8508474576271187
251
295


In [56]:
# When all models are pred red with high confidendce, how often was it red?
print(all_res1.query('''
    HighConfidence_day == True & HighConfidence_30m == True & HighConfidence_1h == True & HighConfidence_90m == True & \
    PredDirection_day == False & PredDirection_30m == False & PredDirection_1h == False & PredDirection_90m == False
''')['RedDays'].sum()  / len(all_res1.query('''
    HighConfidence_day == True & HighConfidence_30m == True & HighConfidence_1h == True & HighConfidence_90m == True & \
    PredDirection_day == False & PredDirection_30m == False & PredDirection_1h == False & PredDirection_90m == False
 ''')))

print(all_res1.query('''
    HighConfidence_day == True & HighConfidence_30m == True & HighConfidence_1h == True & HighConfidence_90m == True & \
    PredDirection_day == False & PredDirection_30m == False & PredDirection_1h == False & PredDirection_90m == False
 ''')['RedDays'].sum())

print(len(all_res1.query('''
    HighConfidence_day == True & HighConfidence_30m == True & HighConfidence_1h == True & HighConfidence_90m == True & \
    PredDirection_day == False & PredDirection_30m == False & PredDirection_1h == False & PredDirection_90m == False
 ''')))

0.9090909090909091
150
165


In [59]:
(165 + 295) / 1077

0.4271123491179202